In [2]:
import ipdb
import numpy as np
import xarray as xr
import matplotlib.pyplot as plt
import pandas as pd
import matplotlib.pylab as pylab
import cartopy
import cartopy.crs as ccrs
from utils import constants as cnst
from eod import msg
from utils import u_grid, u_interpolate as u_int, u_darrays as uda
import datetime
import salem
from salem import get_demo_file, DataLevels, GoogleVisibleMap, Map
import shapely.geometry as shpg
import glob
import pickle as pkl
import os


pylab.rcParams['figure.figsize'] = (50., 50.)
%matplotlib inline

In [1]:
cd ..

/home/ck/pythonWorkspace/proj_CEH


In [3]:
hist = glob.glob(cnst.lmcs_drive + 'CP_models/CP4_WestAfrica/MCS_files/MODELS/CP4/CP4_allHours_historical_5000km2_-50_WAf/*.nc')
fut = glob.glob(cnst.lmcs_drive + 'CP_models/CP4_WestAfrica/MCS_files/MODELS/CP4/CP4_allHours_future_5000km2_-50_WAf/*.nc')

In [5]:
ds = xr.open_dataset('/media/ck/LStorage/global_water/CP_models/CP4_WestAfrica/MCS_files/MODELS/CP4/CP4_allHours_historical_5000km2_-50_WAf/1998-06-01_16:00:00_16.nc')

In [11]:
np.isnan(ds['u_srfc'].values)

array([[ True,  True,  True, ...,  True,  True,  True],
       [ True,  True,  True, ...,  True,  True,  True],
       [ True,  True,  True, ...,  True,  True,  True],
       ...,
       [False, False, False, ..., False, False, False],
       [False, False, False, ..., False, False, False],
       [False, False, False, ..., False, False, False]])

In [ ]:
def cut_kernel(xpos, ypos, arr, date, lon, lat, t, parallax=False, rotate=False):
    
    dist = 70

    kernel = u_arrays.cut_kernel(arr,xpos, ypos,dist)

    kernel3 = kernel - np.nanmean(kernel)

    cnt = np.zeros_like(kernel)
    cnt[np.isfinite(kernel)] = 1

    if kernel.shape != (dist*2+1, dist*2+1):
        return None

    return kernel, kernel3, cnt

In [76]:
cnt = 0
kernel_list = []
kernel3_list = []
cnt_list = []
for hh in hist:
    dbox = xr.open_dataset(hh)
    if np.sum(np.isnan(dbox['u_srfc'].values)) >10:
    
        print(np.sum(np.isnan(dbox['u_srfc'].values)))
        print('Nans, continue!')
        continue
    
    filt = dbox.where(dbox['lsRain_noon']<0.005)
    
    tmin = filt.where(dbox['lw_out_PBLtop']==filt['lw_out_PBLtop'].min(), drop=True)

    #point = dbox.sel(latitude=tmin.latitude, longitude=tmin.longitude, method='nearest')
    plat = tmin['latitude'].values
    plon = tmin['longitude'].values

    xpos = np.where(filt['longitude'].values == plon)
    xpos = int(xpos[0])
    ypos = np.where(filt['latitude'].values == plat)
    ypos = int(ypos[0])

    distx=15 # 500km across
    disty =15# 500 km across
    try:
        filt = filt.isel(latitude=slice(ypos-disty,ypos+disty+1), longitude=slice(xpos-distx, xpos+distx+1))
    except IndexError:
        continue

    if (len(filt.latitude) != disty*2+1) | (len(filt.longitude) != distx*2+1):
        print(filt)
        continue
    filt = filt.assign_coords({'longitude': np.arange(distx*-1,distx+1), 'latitude':np.arange(distx*-1,distx+1)})
    
    kernel_list.append(filt)
    kernel3_list.append(filt-filt.mean())
    
    del filt    
    cnt +=1

4779
Nans, continue!
<xarray.Dataset>
Dimensions:        (latitude: 8, longitude: 8)
Coordinates:
    time           object 1998-06-01 16:30:00
  * latitude       (latitude) float32 14.658001 14.698502 ... 14.941502
  * longitude      (longitude) float32 14.744507 14.785004 ... 15.028015
Data variables:
    lw_out_PBLtop  (latitude, longitude) float64 nan -59.04 -58.05 ... nan nan
    lsRain         (latitude, longitude) float64 nan 9.584e-05 ... nan nan
    shear          (latitude, longitude) float32 nan -0.125 -0.25 ... nan nan
    u_mid          (latitude, longitude) float32 nan -0.5 0.25 ... nan nan nan
    u_srfc         (latitude, longitude) float32 nan -0.375 0.5 ... nan nan nan
    q_mid          (latitude, longitude) float64 nan 5.68 5.91 ... nan nan nan
    t_mid          (latitude, longitude) float64 nan 7.72 7.48 ... nan nan nan
    t_low          (latitude, longitude) float64 nan 25.29 24.89 ... nan nan nan
    t_srfc         (latitude, longitude) float64 nan 32.66 32.33 

<xarray.Dataset>
Dimensions:        (latitude: 20, longitude: 29)
Coordinates:
    time           object 1998-06-01 16:30:00
  * latitude       (latitude) float32 9.960003 10.000504 ... 10.689003 10.729504
  * longitude      (longitude) float32 -5.950989 -5.910492 ... -4.816986
Data variables:
    lw_out_PBLtop  (latitude, longitude) float64 -56.0 -66.4 -71.59 ... nan nan
    lsRain         (latitude, longitude) float64 0.0 0.0 0.0 ... nan nan nan
    shear          (latitude, longitude) float32 -18.25 -18.375 ... -17.125
    u_mid          (latitude, longitude) float32 -15.0 -15.0 ... -13.25 -13.25
    u_srfc         (latitude, longitude) float32 3.25 3.375 3.5 ... 3.625 3.875
    q_mid          (latitude, longitude) float64 4.1 4.1 4.1 ... 2.81 2.81 2.82
    t_mid          (latitude, longitude) float64 6.62 6.62 6.61 ... 6.89 6.88
    t_low          (latitude, longitude) float64 20.28 20.37 ... 21.19 21.51
    t_srfc         (latitude, longitude) float64 25.68 25.7 ... 26.13 25.98
  

<xarray.Dataset>
Dimensions:        (latitude: 22, longitude: 2)
Coordinates:
    time           object 2001-07-05 18:30:00.000013
  * latitude       (latitude) float32 12.066002 12.106503 ... 12.916504
  * longitude      (longitude) float32 7.616516 7.657013
Data variables:
    lw_out_PBLtop  (latitude, longitude) float64 nan nan nan nan ... nan nan nan
    lsRain         (latitude, longitude) float64 nan nan nan nan ... nan nan nan
    shear          (latitude, longitude) float32 -19.0 -19.25 ... -18.5 -18.5
    u_mid          (latitude, longitude) float32 -14.875 -15.0 ... -12.75
    u_srfc         (latitude, longitude) float32 4.125 4.25 3.75 ... 5.625 5.75
    q_mid          (latitude, longitude) float64 6.16 6.18 6.09 ... 5.79 5.72
    t_mid          (latitude, longitude) float64 5.06 5.05 5.04 ... 5.56 5.56
    t_low          (latitude, longitude) float64 20.24 20.29 ... 20.91 20.57
    t_srfc         (latitude, longitude) float64 25.66 25.69 ... 26.35 26.52
    q_srfc         (

3104
Nans, continue!
35
Nans, continue!
54
Nans, continue!
616
Nans, continue!
70
Nans, continue!
337
Nans, continue!
208
Nans, continue!
468
Nans, continue!
13
Nans, continue!
<xarray.Dataset>
Dimensions:        (latitude: 3, longitude: 6)
Coordinates:
    time           object 1999-08-20 23:29:58
  * latitude       (latitude) float32 14.455502 14.496002 14.536503
  * longitude      (longitude) float32 -5.262512 -5.221985 ... -5.0599976
Data variables:
    lw_out_PBLtop  (latitude, longitude) float64 nan nan nan nan ... nan nan nan
    lsRain         (latitude, longitude) float64 nan nan nan nan ... nan nan nan
    shear          (latitude, longitude) float32 -15.375 -15.125 ... -14.75
    u_mid          (latitude, longitude) float32 -11.625 -11.5 ... -11.5 -11.5
    u_srfc         (latitude, longitude) float32 3.75 3.625 3.375 ... 3.25 3.25
    q_mid          (latitude, longitude) float64 6.08 6.09 6.1 ... 6.06 6.07
    t_mid          (latitude, longitude) float64 6.03 6.03 6.03 ... 

<xarray.Dataset>
Dimensions:        (latitude: 0, longitude: 23)
Coordinates:
    time           object 1998-06-02 22:30:00
  * latitude       (latitude) float32 
  * longitude      (longitude) float32 -4.8980103 -4.8575134 ... -4.0069885
Data variables:
    lw_out_PBLtop  (latitude, longitude) float64 
    lsRain         (latitude, longitude) float64 
    shear          (latitude, longitude) float32 
    u_mid          (latitude, longitude) float32 
    u_srfc         (latitude, longitude) float32 
    q_mid          (latitude, longitude) float64 
    t_mid          (latitude, longitude) float64 
    t_low          (latitude, longitude) float64 
    t_srfc         (latitude, longitude) float64 
    q_srfc         (latitude, longitude) float64 
    tcwv           (latitude, longitude) float64 
    sh             (latitude, longitude) float64 
    lh             (latitude, longitude) float64 
    t2             (latitude, longitude) float64 
    q2             (latitude, longitude) floa

...

<xarray.Dataset>
Dimensions:        (latitude: 31, longitude: 22)
Coordinates:
    time           object 2004-07-24 17:29:58
  * latitude       (latitude) float32 12.268501 12.309002 ... 13.483501
  * longitude      (longitude) float32 7.859497 7.899994 ... 8.669495 8.709991
Data variables:
    lw_out_PBLtop  (latitude, longitude) float64 nan nan -51.61 ... nan nan nan
    lsRain         (latitude, longitude) float64 nan nan 0.0 0.0 ... nan nan nan
    shear          (latitude, longitude) float32 -19.75 -20.0 ... -19.25 -19.125
    u_mid          (latitude, longitude) float32 -13.625 -13.5 ... -11.125 -11.0
    u_srfc         (latitude, longitude) float32 6.125 6.5 7.125 ... 8.125 8.125
    q_mid          (latitude, longitude) float64 5.34 5.32 5.3 ... 4.62 4.61 4.6
    t_mid          (latitude, longitude) float64 6.03 6.02 6.02 ... 6.11 6.09
    t_low          (latitude, longitude) float64 19.42 19.39 ... 20.88 20.91
    t_srfc         (latitude, longitude) float64 25.14 24.98 ... 27.

<xarray.Dataset>
Dimensions:        (latitude: 3, longitude: 0)
Coordinates:
    time           object 2004-07-24 18:30:00.000013
  * latitude       (latitude) float32 8.623501 8.664001 8.704502
  * longitude      (longitude) float32 
Data variables:
    lw_out_PBLtop  (latitude, longitude) float64 
    lsRain         (latitude, longitude) float64 
    shear          (latitude, longitude) float32 
    u_mid          (latitude, longitude) float32 
    u_srfc         (latitude, longitude) float32 
    q_mid          (latitude, longitude) float64 
    t_mid          (latitude, longitude) float64 
    t_low          (latitude, longitude) float64 
    t_srfc         (latitude, longitude) float64 
    q_srfc         (latitude, longitude) float64 
    tcwv           (latitude, longitude) float64 
    sh             (latitude, longitude) float64 
    lh             (latitude, longitude) float64 
    t2             (latitude, longitude) float64 
    q2             (latitude, longitude) float64 

<xarray.Dataset>
Dimensions:        (latitude: 10, longitude: 20)
Coordinates:
    time           object 2006-08-03 18:30:00.000013
  * latitude       (latitude) float32 4.047001 4.0875015 ... 4.371002 4.411503
  * longitude      (longitude) float32 17.053009 17.093506 ... 17.82251
Data variables:
    lw_out_PBLtop  (latitude, longitude) float64 -66.93 -67.28 -67.6 ... nan nan
    lsRain         (latitude, longitude) float64 1.298 1.102 1.205 ... nan nan
    shear          (latitude, longitude) float32 -9.0 -9.0 ... -9.625 -9.75
    u_mid          (latitude, longitude) float32 -5.375 -5.375 ... -6.0 -6.0
    u_srfc         (latitude, longitude) float32 3.625 3.625 ... 3.625 3.75
    q_mid          (latitude, longitude) float64 6.89 6.9 6.91 ... 6.81 6.78
    t_mid          (latitude, longitude) float64 4.6 4.58 4.58 ... 4.71 4.75
    t_low          (latitude, longitude) float64 18.27 17.84 ... 18.53 18.7
    t_srfc         (latitude, longitude) float64 23.94 24.09 ... 24.07 23.97
    q

/home/ck/miniconda3/lib/python3.7/site-packages/ipykernel_launcher.py:21: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.


TypeError: only size-1 arrays can be converted to Python scalars

In [ ]:
kk = xr.concat(kernel_list, dim='cases')

In [ ]:
(kk.mean('cases')['t_low']-kk.mean('cases')['t_mid']).plot()

In [ ]:
kk2 = xr.concat(kernel3_list, dim='cases')

In [ ]:
kk2.mean('cases')['t2'].plot()

In [ ]:
cnt = 0
futkernel_list = []
futkernel3_list = []
cnt_list = []
for hh in fut:
    dbox = xr.open_dataset(hh)
    if np.sum(np.isnan(dbox['u_srfc'].values)) >10:
    
        print(np.sum(np.isnan(dbox['u_srfc'].values)))
        print('Nans, continue!')
        continue
    
    filt = dbox.where(dbox['lsRain_noon']<0.005)
    
    tmin = filt.where(dbox['lw_out_PBLtop']==filt['lw_out_PBLtop'].min(), drop=True)

    #point = dbox.sel(latitude=tmin.latitude, longitude=tmin.longitude, method='nearest')
    plat = tmin['latitude'].values
    plon = tmin['longitude'].values

    xpos = np.where(filt['longitude'].values == plon)
    xpos = int(xpos[0])
    ypos = np.where(filt['latitude'].values == plat)
    ypos = int(ypos[0])

    distx=15 # 500km across
    disty =15 # 500 km across
    try:
        filt = filt.isel(latitude=slice(ypos-disty,ypos+disty+1), longitude=slice(xpos-distx, xpos+distx+1))
    except IndexError:
        continue

    if (len(filt.latitude) != disty*2+1) | (len(filt.longitude) != distx*2+1):
        print(filt)
        continue
    filt = filt.assign_coords({'longitude': np.arange(distx*-1,distx+1), 'latitude':np.arange(distx*-1,distx+1)})
    
    futkernel_list.append(filt)
    futkernel3_list.append(filt-filt.mean())
    
    del filt    
    cnt +=1

In [ ]:
futkk = xr.concat(futkernel_list, dim='cases')

In [ ]:
futkk

In [ ]:
futkk.mean('cases')['shear'].plot()